In [26]:
import note_seq
from magenta.models.melody_rnn import melody_rnn_sequence_generator
from magenta.models.performance_rnn import performance_sequence_generator
from magenta.models.shared import sequence_generator_bundle
from note_seq.protobuf import generator_pb2

In [19]:
SF2_PATH = 'soundfonts/Yamaha-C5-Salamander-JNv5.1.sf2'
SAMPLE_RATE = float(44100)

# MelodyRNN

In [4]:
note_seq.notebook_utils.download_bundle("basic_rnn.mag", "models/music_rnn/")

In [7]:
bundle = sequence_generator_bundle.read_bundle_file('models/music_rnn/basic_rnn.mag')
generator_map = melody_rnn_sequence_generator.get_generator_map()
melody_rnn = generator_map['basic_rnn'](checkpoint=None, bundle=bundle)
melody_rnn.initialize()

'model_variables' collection should be of type 'byte_list', but instead is of type 'node_list'.
INFO:tensorflow:Restoring parameters from /var/folders/m3/6svr5sf15rv9b8y0fpsbygfw0000gp/T/tmp6mylnor0/model.ckpt


2023-06-08 16:16:50.309006: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArray is deprecated. It will cease to work in GraphDef version 16. Use TensorArrayV3.
2023-06-08 16:16:50.309107: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArrayScatter is deprecated. It will cease to work in GraphDef version 19. Use TensorArrayGradV3.
2023-06-08 16:16:50.309213: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArrayRead is deprecated. It will cease to work in GraphDef version 16. Use TensorArrayReadV3.
2023-06-08 16:16:50.309696: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArrayWrite is deprecated. It will cease to work in GraphDef version 16. Use TensorArrayWriteV3.
2023-06-08 16:16:50.309779: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArraySize is deprecated. It will cease to work in GraphDef version 16. Use TensorArraySizeV3.
2023-06-08 16:16:50.309809: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArrayGather is deprecat

In [8]:
input_sequence = note_seq.midi_file_to_note_sequence('data/clair_de_lune.mid')

In [10]:
num_steps = 128 # change this for shorter or longer sequences
temperature = 1.0 # the higher the temperature the more random the sequence.

In [12]:
last_end_time = (max(n.end_time for n in input_sequence.notes) if input_sequence.notes else 0)
qpm = input_sequence.tempos[0].qpm 
seconds_per_step = 60.0 / qpm / melody_rnn.steps_per_quarter
total_seconds = num_steps * seconds_per_step

In [15]:
generator_options = generator_pb2.GeneratorOptions()
generator_options.args['temperature'].float_value = temperature
generate_section = generator_options.generate_sections.add(
  start_time=last_end_time + seconds_per_step,
  end_time=total_seconds
)

In [16]:
sequence = melody_rnn.generate(input_sequence, generator_options)

INFO:tensorflow:Beam search yields sequence with log-likelihood: -89.369087 


2023-06-08 16:30:27.349391: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArray is deprecated. It will cease to work in GraphDef version 16. Use TensorArrayV3.
2023-06-08 16:30:27.349748: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArrayScatter is deprecated. It will cease to work in GraphDef version 19. Use TensorArrayGradV3.
2023-06-08 16:30:27.350088: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArrayRead is deprecated. It will cease to work in GraphDef version 16. Use TensorArrayReadV3.
2023-06-08 16:30:27.350103: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArraySize is deprecated. It will cease to work in GraphDef version 16. Use TensorArraySizeV3.
2023-06-08 16:30:27.350349: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArrayGather is deprecated. It will cease to work in GraphDef version 16. Use TensorArrayGatherV3.
2023-06-08 16:30:27.351286: W tensorflow/core/framework/op_def_util.cc:369] Op TensorArrayWrite is depreca

In [20]:
note_seq.play_sequence(sequence, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(sequence)

Loading BokehJS ...

# Performance RNN

In [21]:
note_seq.notebook_utils.download_bundle("performance_with_dynamics.mag", "models/performance_rnn/")

In [23]:
bundle = sequence_generator_bundle.read_bundle_file('models/performance_rnn/performance_with_dynamics.mag')
generator_map = performance_sequence_generator.get_generator_map()
generator = generator_map['performance_with_dynamics'](checkpoint=None, bundle=bundle)
generator.initialize()

'model_variables' collection should be of type 'byte_list', but instead is of type 'node_list'.
INFO:tensorflow:Restoring parameters from /var/folders/m3/6svr5sf15rv9b8y0fpsbygfw0000gp/T/tmprciikz_p/model.ckpt


In [36]:
input_sequence = note_seq.midi_file_to_note_sequence('data/clair_de_lune.mid')

In [ ]:
temperature = 1.0

In [38]:
last_end_time = (max(n.end_time for n in input_sequence.notes) if input_sequence.notes else 0)
seconds_per_step = 0.1
total_seconds = 30

In [39]:
generator_options = generator_pb2.GeneratorOptions()
generator_options.args['temperature'].float_value = temperature # Higher is more random; 1.0 is default. 
generate_section = generator_options.generate_sections.add(start_time=last_end_time + seconds_per_step, end_time=total_seconds)

In [40]:
sequence = generator.generate(input_sequence, generator_options)

INFO:tensorflow:Need to generate 2309 more steps for this sequence, will try asking for 1386 RNN steps


INFO:tensorflow:Need to generate 2309 more steps for this sequence, will try asking for 1386 RNN steps


INFO:tensorflow:Beam search yields sequence with log-likelihood: -3247.928711 


INFO:tensorflow:Beam search yields sequence with log-likelihood: -3247.928711 


In [41]:
note_seq.play_sequence(sequence, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)
note_seq.plot_sequence(sequence)

Loading BokehJS ...